In [1]:
import yfinance as yf
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import norm
from scipy.interpolate import griddata
import datetime

# ========================
# Black-Scholes Greeks Calculator
# ========================
def black_scholes_greeks(S, K, T, r, sigma, option_type='call'):
    T = max(T, 1e-3)  # Avoid division by zero
    
    d1 = (np.log(S / K) + (r + 0.5 * sigma**2) * T) / (sigma * np.sqrt(T))
    d2 = d1 - sigma * np.sqrt(T)
    
    N_d1 = norm.cdf(d1)
    N_d2 = norm.cdf(d2)
    N_prime_d1 = norm.pdf(d1)
    
    if option_type == 'call':
        delta = N_d1
        theta = (-S * N_prime_d1 * sigma / (2 * np.sqrt(T)) 
                 - r * K * np.exp(-r * T) * N_d2) / 365  # Per day
        rho = K * T * np.exp(-r * T) * N_d2 / 100  # Per 1% rate change
    else:
        delta = N_d1 - 1
        theta = (-S * N_prime_d1 * sigma / (2 * np.sqrt(T)) 
                 + r * K * np.exp(-r * T) * norm.cdf(-d2)) / 365
        rho = -K * T * np.exp(-r * T) * norm.cdf(-d2) / 100
    
    gamma = N_prime_d1 / (S * sigma * np.sqrt(T))
    vega = S * np.sqrt(T) * N_prime_d1 / 100  # Per 1% volatility change
    
    return {
        'delta': delta,
        'gamma': gamma,
        'theta': theta,
        'vega': vega,
        'rho': rho
    }

# ========================
# Fetch Data & Compute Greeks
# ========================
def fetch_and_compute_greeks(ticker='SPY', risk_free_rate=0.03):
    stock = yf.Ticker(ticker)
    S = stock.history(period='1d')['Close'].iloc[-1]  # Current price
    exp_dates = stock.options
    
    strikes = []
    ttes = []
    ivs = []
    greeks = []
    
    for exp_date_str in exp_dates:
        try:
            chain = stock.option_chain(exp_date_str).calls  # Use calls (change to puts if needed)
            exp_date = datetime.datetime.strptime(exp_date_str, "%Y-%m-%d").date()
            today = datetime.date.today()
            T = (exp_date - today).days / 365.0
            
            for _, row in chain.iterrows():
                K = row['strike']
                sigma = row['impliedVolatility']
                
                # Compute Greeks
                greek = black_scholes_greeks(S, K, T, risk_free_rate, sigma, 'call')
                greeks.append(greek)
                strikes.append(K)
                ttes.append(T)
                ivs.append(sigma)
                
        except Exception as e:
            print(f"Skipping {exp_date_str}: {e}")
            continue
    
    return {
        'strikes': np.array(strikes),
        'ttes': np.array(ttes),
        'ivs': np.array(ivs),
        'greeks': greeks,
        'spot_price': S
    }

# ========================
# Interactive Plotting
# ========================
def create_greek_surface(data, greek_name, title_suffix):
    strikes = data['strikes']
    ttes = data['ttes']
    greek_values = np.array([g[greek_name] for g in data['greeks']])
    
    # Interpolate onto grid
    grid_strikes, grid_tes = np.meshgrid(
        np.linspace(strikes.min(), strikes.max(), 100),
        np.linspace(ttes.min(), ttes.max(), 100)
    )
    grid_values = griddata(
        (strikes, ttes), greek_values,
        (grid_strikes, grid_tes),
        method='cubic'
    )
    
    # 3D Surface
    surface = go.Surface(
        x=grid_strikes,
        y=grid_tes,
        z=grid_values,
        colorscale='Viridis',
        name='3D Surface',
        hovertemplate="Strike: %{x}<br>TTE: %{y:.2f} yrs<br>Value: %{z:.4f}<extra></extra>"
    )
    
    # 2D Slice (closest to spot price)
    S = data['spot_price']
    closest_strike_idx = np.abs(strikes - S).argmin()
    ttes_slice = ttes[closest_strike_idx::len(np.unique(strikes))]
    greek_slice = greek_values[closest_strike_idx::len(np.unique(strikes))]
    
    line = go.Scatter(
        x=ttes_slice,
        y=greek_slice,
        mode='lines+markers',
        name='2D Slice (Near Spot)',
        line=dict(color='red'),
        hovertemplate="TTE: %{x:.2f} yrs<br>Value: %{y:.4f}<extra></extra>"
    )
    
    # Subplots
    fig = make_subplots(
        rows=1, cols=2,
        specs=[[{'type': 'surface'}, {'type': 'xy'}]],
        subplot_titles=(
            f'3D {greek_name} Surface',
            f'2D {greek_name} vs. Time (Strike ≈ {S:.1f})'
        )
    )
    
    fig.add_trace(surface, row=1, col=1)
    fig.add_trace(line, row=1, col=2)
    
    fig.update_layout(
        title=f'{greek_name} Analysis: {title_suffix}',
        width=1400,
        height=700,
        margin=dict(l=50, r=50, b=50, t=100),
        scene=dict(
            xaxis_title='Strike Price',
            yaxis_title='Time to Expiry (years)',
            zaxis_title=greek_name,
            camera=dict(eye=dict(x=1.5, y=1.5, z=0.5))
        ),
        xaxis_title='Time to Expiry (years)',
        yaxis_title=greek_name
    )
    
    return fig

# ========================
# Main Execution
# ========================
if __name__ == '__main__':
    # Fetch data and compute Greeks
    data = fetch_and_compute_greeks(ticker='SPY', risk_free_rate=0.03)
    
    # Generate plots for each Greek
    greeks_to_plot = ['delta', 'gamma', 'theta', 'vega', 'rho']
    
    for greek in greeks_to_plot:
        fig = create_greek_surface(data, greek, 'SPY Call Options')
        fig.show(config={'scrollZoom': True})

In [2]:
import yfinance as yf
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import norm

# ========================
# Black-Scholes Greeks Calculator
# ========================
def black_scholes_greeks(S, K, T, r, sigma, option_type='call'):
    T = max(T, 1e-3)  # Avoid division by zero
    
    d1 = (np.log(S / K) + (r + 0.5 * sigma**2) * T) / (sigma * np.sqrt(T))
    d2 = d1 - sigma * np.sqrt(T)
    
    N_d1 = norm.cdf(d1)
    N_d2 = norm.cdf(d2)
    N_prime_d1 = norm.pdf(d1)
    
    if option_type == 'call':
        delta = N_d1
        theta = (-S * N_prime_d1 * sigma / (2 * np.sqrt(T)) 
                 - r * K * np.exp(-r * T) * N_d2) / 365  # Per day
        rho = K * T * np.exp(-r * T) * N_d2 / 100  # Per 1% rate change
    else:
        delta = N_d1 - 1
        theta = (-S * N_prime_d1 * sigma / (2 * np.sqrt(T)) 
                 + r * K * np.exp(-r * T) * norm.cdf(-d2)) / 365
        rho = -K * T * np.exp(-r * T) * norm.cdf(-d2) / 100
    
    gamma = N_prime_d1 / (S * sigma * np.sqrt(T))
    vega = S * np.sqrt(T) * N_prime_d1 / 100  # Per 1% volatility change
    
    return {
        'delta': delta,
        'gamma': gamma,
        'theta': theta,
        'vega': vega,
        'rho': rho
    }

# ========================
# Generate Theoretical Data
# ========================
def generate_theoretical_greeks(spot_price=100, risk_free_rate=0.03, 
                               volatility=0.2, option_type='call'):
    # Create synthetic grid
    strikes = np.linspace(spot_price * 0.5, spot_price * 1.5, 100)
    ttes = np.linspace(0.1, 2, 100)  # 0.1 to 2 years
    strikes_grid, ttes_grid = np.meshgrid(strikes, ttes)
    
    # Flatten grids for computation
    strikes_flat = strikes_grid.flatten()
    ttes_flat = ttes_grid.flatten()
    
    greeks = []
    for K, T in zip(strikes_flat, ttes_flat):
        greek = black_scholes_greeks(
            spot_price, K, T, risk_free_rate, volatility, option_type
        )
        greeks.append(greek)
    
    return {
        'strikes': strikes_flat,
        'ttes': ttes_flat,
        'greeks': greeks,
        'spot_price': spot_price,
        'strikes_grid': strikes_grid,
        'ttes_grid': ttes_grid
    }

# ========================
# Interactive Plotting
# ========================
def plot_theoretical_greeks(data, greek_name):
    # Reshape Greek values to match grid
    greek_values = np.array([g[greek_name] for g in data['greeks']])
    greek_grid = greek_values.reshape(data['strikes_grid'].shape)
    
    # Create 3D surface
    surface = go.Surface(
        x=data['strikes_grid'],
        y=data['ttes_grid'],
        z=greek_grid,
        colorscale='Viridis',
        hovertemplate="Strike: %{x}<br>TTE: %{y:.2f} yrs<br>Value: %{z:.4f}<extra></extra>"
    )
    
    # 2D slice at spot price
    S = data['spot_price']
    closest_strike_idx = np.abs(data['strikes_grid'][0,:] - S).argmin()
    ttes_slice = data['ttes_grid'][:,0]
    greek_slice = greek_grid[:, closest_strike_idx]
    
    line = go.Scatter(
        x=ttes_slice,
        y=greek_slice,
        mode='lines+markers',
        line=dict(color='red'),
        hovertemplate="TTE: %{x:.2f} yrs<br>Value: %{y:.4f}<extra></extra>"
    )
    
    # Create subplots
    fig = make_subplots(
        rows=1, cols=2,
        specs=[[{'type': 'surface'}, {'type': 'xy'}]],
        subplot_titles=(
            f'Theoretical {greek_name} Surface',
            f'{greek_name} vs. Time (Strike = {data["strikes_grid"][0,closest_strike_idx]:.1f})'
        )
    )
    
    fig.add_trace(surface, row=1, col=1)
    fig.add_trace(line, row=1, col=2)
    
    fig.update_layout(
        width=1400,
        height=700,
        margin=dict(l=50, r=50, b=50, t=100),
        scene=dict(
            xaxis_title='Strike Price',
            yaxis_title='Time to Expiry (years)',
            zaxis_title=greek_name,
            camera=dict(eye=dict(x=1.5, y=1.5, z=0.5))
        ),
        xaxis_title='Time to Expiry (years)',
        yaxis_title=greek_name
    )
    
    return fig

# ========================
# Main Execution
# ========================
if __name__ == '__main__':
    # Get current SPY price for realistic example
    spy = yf.Ticker("SPY")
    spot_price = spy.history(period='1d')['Close'].iloc[-1]
    
    # Generate theoretical data (modify parameters as needed)
    data = generate_theoretical_greeks(
        spot_price=spot_price,
        risk_free_rate=0.03,
        volatility=0.2,  # Set your implied volatility here
        option_type='call'
    )
    
    # Plot all Greeks
    for greek in ['delta', 'gamma', 'theta', 'vega', 'rho']:
        fig = plot_theoretical_greeks(data, greek)
        fig.show(config={'scrollZoom': True})

In [3]:
import yfinance as yf
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import norm
from scipy.interpolate import griddata
import datetime

# ========================
# Black-Scholes Greeks Calculator
# ========================
def black_scholes_greeks(S, K, T, r, sigma, option_type='call'):
    T = max(T, 1e-3)  # Avoid division by zero
    
    d1 = (np.log(S / K) + (r + 0.5 * sigma**2) * T) / (sigma * np.sqrt(T))
    d2 = d1 - sigma * np.sqrt(T)
    
    N_d1 = norm.cdf(d1)
    N_d2 = norm.cdf(d2)
    N_prime_d1 = norm.pdf(d1)
    
    if option_type == 'call':
        delta = N_d1
        theta = (-S * N_prime_d1 * sigma / (2 * np.sqrt(T)) 
                 - r * K * np.exp(-r * T) * N_d2) / 365  # Per day
        rho = K * T * np.exp(-r * T) * N_d2 / 100  # Per 1% rate change
    else:
        delta = N_d1 - 1
        theta = (-S * N_prime_d1 * sigma / (2 * np.sqrt(T)) 
                 + r * K * np.exp(-r * T) * norm.cdf(-d2)) / 365
        rho = -K * T * np.exp(-r * T) * norm.cdf(-d2) / 100
    
    gamma = N_prime_d1 / (S * sigma * np.sqrt(T))
    vega = S * np.sqrt(T) * N_prime_d1 / 100  # Per 1% volatility change
    
    return {
        'delta': delta,
        'gamma': gamma,
        'theta': theta,
        'vega': vega,
        'rho': rho
    }

# ========================
# Fetch Market Data & Compute Greeks
# ========================
def fetch_market_greeks(ticker='SPY', risk_free_rate=0.03):
    stock = yf.Ticker(ticker)
    S = stock.history(period='1d')['Close'].iloc[-1]  # Current price
    exp_dates = stock.options
    
    strikes, ttes, ivs, mkt_greeks = [], [], [], []
    
    for exp_date_str in exp_dates[:3]:  # Limit to 3 expiries for speed
        try:
            chain = stock.option_chain(exp_date_str).calls  # Use calls
            exp_date = datetime.datetime.strptime(exp_date_str, "%Y-%m-%d").date()
            today = datetime.date.today()
            T = (exp_date - today).days / 365.0
            
            for _, row in chain.iterrows():
                K = row['strike']
                sigma_mkt = row['impliedVolatility']
                
                # Compute Market Greeks (using market IV)
                greek_mkt = black_scholes_greeks(S, K, T, risk_free_rate, sigma_mkt, 'call')
                
                strikes.append(K)
                ttes.append(T)
                ivs.append(sigma_mkt)
                mkt_greeks.append(greek_mkt)
                
        except Exception as e:
            print(f"Skipping {exp_date_str}: {e}")
            continue
    
    return {
        'strikes': np.array(strikes),
        'ttes': np.array(ttes),
        'ivs': np.array(ivs),
        'mkt_greeks': mkt_greeks,
        'spot_price': S
    }

# ========================
# Generate Theoretical Greeks (Flat Volatility Assumption)
# ========================
def generate_theoretical_greeks(data, theoretical_vol=0.2, risk_free_rate=0.03):
    S = data['spot_price']
    strikes = data['strikes']
    ttes = data['ttes']
    theo_greeks = []
    
    for K, T in zip(strikes, ttes):
        # Compute Theoretical Greeks (flat volatility)
        greek_theo = black_scholes_greeks(S, K, T, risk_free_rate, theoretical_vol, 'call')
        theo_greeks.append(greek_theo)
    
    return theo_greeks

# ========================
# Interactive Comparison Plots
# ========================
def plot_greek_comparison(data, theo_greeks, greek_name):
    strikes = data['strikes']
    ttes = data['ttes']
    mkt_values = np.array([g[greek_name] for g in data['mkt_greeks']])
    theo_values = np.array([g[greek_name] for g in theo_greeks])
    
    # Grid interpolation for surfaces
    grid_strikes, grid_tes = np.meshgrid(
        np.linspace(strikes.min(), strikes.max(), 50),
        np.linspace(ttes.min(), ttes.max(), 50)
    )
    
    # Market surface
    grid_mkt = griddata(
        (strikes, ttes), mkt_values,
        (grid_strikes, grid_tes), method='linear'
    )
    
    # Theoretical surface
    grid_theo = griddata(
        (strikes, ttes), theo_values,
        (grid_strikes, grid_tes), method='linear'
    )
    
    # Create subplots
    fig = make_subplots(
        rows=1, cols=2,
        specs=[[{'type': 'surface'}, {'type': 'surface'}]],
        subplot_titles=(
            f'Market-Implied {greek_name} (Real)',
            f'Theoretical {greek_name} (Flat Volatility)'
        )
    )
    
    # Market plot
    fig.add_trace(go.Surface(
        x=grid_strikes, y=grid_tes, z=grid_mkt,
        colorscale='Viridis', name='Market',
        hovertemplate="Strike: %{x}<br>TTE: %{y:.2f} yrs<br>Market: %{z:.4f}<extra></extra>"
    ), row=1, col=1)
    
    # Theoretical plot
    fig.add_trace(go.Surface(
        x=grid_strikes, y=grid_tes, z=grid_theo,
        colorscale='Viridis', name='Theoretical',
        hovertemplate="Strike: %{x}<br>TTE: %{y:.2f} yrs<br>Theoretical: %{z:.4f}<extra></extra>"
    ), row=1, col=2)
    
    fig.update_layout(
        title=f'{greek_name} Comparison: Market vs. Theoretical (Arbitrage Detection)',
        width=1400,
        height=700,
        margin=dict(l=50, r=50, b=50, t=100),
        scene1=dict(
            xaxis_title='Strike',
            yaxis_title='TTE (years)',
            zaxis_title='Market Value',
            camera=dict(eye=dict(x=1.5, y=1.5, z=0.5))
        ),
        scene2=dict(
            xaxis_title='Strike',
            yaxis_title='TTE (years)',
            zaxis_title='Theoretical Value',
            camera=dict(eye=dict(x=1.5, y=1.5, z=0.5))
        )
    )
    
    # Add delta surface (difference) for arbitrage
    delta_grid = grid_mkt - grid_theo
    delta_fig = go.Figure(data=[go.Surface(
        x=grid_strikes, y=grid_tes, z=delta_grid,
        colorscale='RdBu', 
        hovertemplate="Strike: %{x}<br>TTE: %{y:.2f} yrs<br>Δ: %{z:.4f}<extra></extra>"
    )])
    delta_fig.update_layout(
        title=f'{greek_name} Difference (Market - Theoretical)',
        scene=dict(
            xaxis_title='Strike',
            yaxis_title='TTE (years)',
            zaxis_title='Δ Value'
        )
    )
    
    return fig, delta_fig

# ========================
# Main Execution
# ========================
if __name__ == '__main__':
    # Fetch market data and compute Greeks
    data = fetch_market_greeks(ticker='SPY', risk_free_rate=0.03)
    
    # Generate theoretical Greeks (using average market IV)
    avg_vol = np.mean(data['ivs'])
    theo_greeks = generate_theoretical_greeks(data, theoretical_vol=avg_vol)
    
    # Plot comparisons for all Greeks
    for greek in ['delta', 'gamma', 'theta', 'vega', 'rho']:
        comp_fig, delta_fig = plot_greek_comparison(data, theo_greeks, greek)
        comp_fig.show()
        delta_fig.show()